Katie Mears and Dip Bista <br>
ADS507 Final Project <br>
California Job Listings and Median Average Income <br>

Data downloaded from the following sources: 

California State Jobs csv from Kaggle.com - https://www.kaggle.com/datasets/datasciencedonut/california-state-jobs <br>
Median Prices of Existing Single Family Homes - https://www.car.org/en/marketdata/data/housingdata <br>
2023 Income Limits by County from CA.gov website - https://data.ca.gov/dataset/income-limits-by-county <br>

GitHub Link: https://github.com/DiprajBista/ADS-507-Group-2-Final-Project-.git

Installing and Importing Packages

In [1]:
# pip install plotly
# ! pip install nbformat
# ! pip install --upgrade nbformat
# ! pip install dash
# pip install dash plotly

In [2]:

from IPython.display import HTML
from IPython.display import display
import pandas as pd 
import pymysql as mysql
import matplotlib.pyplot as plt 
import warnings
import folium
from geopy.geocoders import Nominatim
import plotly.express as px
import nbformat
import dash
from dash import html, dcc
from dash.dependencies import Input, Output



C:\Users\katie\AppData\Local\Temp\ipykernel_34776\2387725768.py:3: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd


## Set Up 

Establish the connection to ca_job_listings database through Azure 

In [3]:
import mysql.connector  
cnx = mysql.connector.connect(user="admin507", 
                              password="finalproject507!", 
                              host="jobsfinal507.mysql.database.azure.com", 
                              port=3306, 
                              database="ca_job_listings")

# Display a message indicating a successful connection
print("Connected to ca_job_listings Azure Database")

Connected to ca_job_listings Azure Database


In [4]:
# Show tables in the ca_job_listings database
cursor = cnx.cursor()
query = "SHOW TABLES"
cursor.execute(query)
tables = cursor.fetchall()
for table in tables:
    print(table[0])

average_median_income
combined_data
combined_data_with_home_price
household_income
housing_data
job_salary_location
jobs
transposed_housing_data


# Create Data Frames for required Tables 

In [5]:
# Create Dataframe for job_salary_location table in ca_job_listings database 
query = "SELECT my_row_id, Job_ID, Working_title, Salary, avg_annual_salary, Location FROM job_salary_location"

job_salary_location_df = pd.read_sql(query, cnx)
print(job_salary_location_df)

C:\Users\katie\AppData\Local\Temp\ipykernel_34776\3984061199.py:4: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  job_salary_location_df = pd.read_sql(query, cnx)


       my_row_id  Job_ID                             Working_title  \
0              1       1    Associate Governmental Program Analyst   
1              2       2    Associate Governmental Program Analyst   
2              3       3                   AGPA - Contract Analyst   
3              4       6                        Senior Tax Auditor   
4              5       7                        Senior Tax Auditor   
...          ...     ...                                       ...   
26439      26440   27855                                Podiatrist   
26440      26441   27856              Assistive Technology Trainee   
26441      26442   27858  Custodian I -Metropolitan State Hospital   
26442      26443   27859                                  SVRC/QRP   
26443      26444   27860                 FOOD SERVICE SUPERVISOR I   

                    Salary  avg_annual_salary      Location  
0        5684.00 - 7114.00              76788   Sacramento   
1        5518.00 - 6907.00         

In [6]:
# Create Dataframe for combined_data table in ca_job_listings database 
query = "SELECT Job_ID, avg_annual_salary, County_ID, County, Avg_Median_Income FROM combined_data"

combined_df = pd.read_sql(query, cnx)
print(combined_df)

       Job_ID  avg_annual_salary  County_ID       County  Avg_Median_Income
0           1              76788         34   Sacramento             113900
1           2              74556         10       Fresno              83800
2           3              76788         34   Sacramento             113900
3           6             102540         19  Los Angeles              98200
4           7             104976         19  Los Angeles              98200
...       ...                ...        ...          ...                ...
26439   27855             200316         54       Tulare              83800
26440   27856              45504         54       Tulare              83800
26441   27858              39540         19  Los Angeles              98200
26442   27859              67812         21        Marin             175000
26443   27860              43176         19  Los Angeles              98200

[26444 rows x 5 columns]


C:\Users\katie\AppData\Local\Temp\ipykernel_34776\3775237855.py:4: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  combined_df = pd.read_sql(query, cnx)


In [7]:
# Create Dataframe for combined_data_with_home_price table in ca_job_listings database 
query = "SELECT Job_ID, working_title, avg_annual_salary, County_ID, County, Avg_Median_Income, Home_Price_Average FROM combined_data_with_home_price"

combined_with_home_price_df = pd.read_sql(query, cnx)
print(combined_with_home_price_df )

C:\Users\katie\AppData\Local\Temp\ipykernel_34776\1975908079.py:4: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  combined_with_home_price_df = pd.read_sql(query, cnx)


       Job_ID                             working_title  avg_annual_salary  \
0           1    Associate Governmental Program Analyst              76788   
1           2    Associate Governmental Program Analyst              74556   
2           3                   AGPA - Contract Analyst              76788   
3           6                        Senior Tax Auditor             102540   
4           7                        Senior Tax Auditor             104976   
...       ...                                       ...                ...   
26439   27855                                Podiatrist             200316   
26440   27856              Assistive Technology Trainee              45504   
26441   27858  Custodian I -Metropolitan State Hospital              39540   
26442   27859                                  SVRC/QRP              67812   
26443   27860                 FOOD SERVICE SUPERVISOR I              43176   

       County_ID       County  Avg_Median_Income  Home_Price_Av

# job_salary_location Visualizations 

In [8]:
# Calculate the number of jobs per county
county_jobs = job_salary_location_df.groupby('Location').size().reset_index(name='Number_of_Jobs')

# Sort the DataFrame in descending order based on the number of jobs
county_jobs_sorted = county_jobs.sort_values(by='Number_of_Jobs', ascending=False)

# Create an interactive bar chart using Plotly
fig = px.bar(county_jobs_sorted, x='Location', y='Number_of_Jobs', title='Number of Jobs per County', color='Location')
fig.update_layout(xaxis_title='County', yaxis_title='Number of Jobs')
fig.update_xaxes(tickangle=90)
fig.show()

# print(county_jobs_sorted)

In [9]:
# Filter the DataFrame based on the requirement
filtered_df = combined_with_home_price_df[combined_with_home_price_df['avg_annual_salary'] > combined_with_home_price_df['Avg_Median_Income']]

# Calculate the number of jobs per county for the filtered DataFrame
county_jobs_filtered = filtered_df.groupby('County').size().reset_index(name='Number_of_Jobs')

# Sort the DataFrame in descending order based on the number of jobs
county_jobs_filtered_sorted = county_jobs_filtered.sort_values(by='Number_of_Jobs', ascending=False)

# Create an interactive bar chart using Plotly
fig = px.bar(county_jobs_filtered_sorted, x='County', y='Number_of_Jobs', title='Number of Jobs per County where Average Salary > Average Median Income', color='County')
fig.update_layout(xaxis_title='County', yaxis_title='Number of Jobs')
fig.update_xaxes(tickangle=90)
fig.show()

In [10]:
# Calculate the average salary per county
county_avg_salary = job_salary_location_df.groupby('Location')['avg_annual_salary'].mean().reset_index()

# Sort the DataFrame in descending order based on average salary
county_avg_salary_sorted = county_avg_salary.sort_values(by='avg_annual_salary', ascending=False)

# Plot the data as an interactive bar chart
fig = px.bar(county_avg_salary_sorted, x='Location', y='avg_annual_salary', color='Location',
             title='Average Salary per County', labels={'avg_annual_salary': 'Average Salary ($)'},
             hover_data={'avg_annual_salary': True})

# Update layout for better readability
fig.update_layout(xaxis_tickangle=-45)

# Show the plot
fig.show()

In [11]:
import plotly.graph_objects as go

# combined_with_home_price Visualizations 

In [12]:
# Calculate the average median income per county
county_AMI = combined_with_home_price_df.groupby('County')['Avg_Median_Income'].mean().reset_index()

# Sort the DataFrame in descending order based on the average median income
county_AMI_sorted = county_AMI.sort_values(by='Avg_Median_Income', ascending=False)

# Plot the data as an interactive bar chart
fig = px.bar(county_AMI_sorted, x='County', y='Avg_Median_Income', color='County',
             title='Average Median Income per County', labels={'Avg_Median_Income': 'Average Salary ($)'},
             hover_data={'Avg_Median_Income': True})

# Update layout for better readability
fig.update_layout(xaxis_tickangle=-45)

# Show the plot
fig.show()

# print(county_AMI_sorted)

In [13]:
# Calculate the average median income per county
avg_homeprice = combined_with_home_price_df.groupby('County')['Home_Price_Average'].mean().reset_index()

# Sort the DataFrame in descending order based on the average median income
avg_homeprice_sorted = avg_homeprice.sort_values(by='Home_Price_Average', ascending=False)

# Plot the data as an interactive bar chart
fig = px.bar(avg_homeprice_sorted, x='County', y='Home_Price_Average', color='County',
             title='Average Home Price per County', labels={'Home_Price_Average': 'Average Home Price ($)'},
             hover_data={'Home_Price_Average': True})

# Update layout for better readability
fig.update_layout(xaxis_tickangle=-45)

# Show the plot
fig.show()

# print(avg_homeprice_sorted)

In [14]:
# Drop the 'County_ID' column from combined_with_home_price_df
combined_with_home_price_df = combined_with_home_price_df.drop(columns=['County_ID'])


In [15]:
# Interactive Table for all Job Postings
fig = go.Figure(data=[go.Table(
    header=dict(values=list(combined_with_home_price_df.columns),
                fill_color='paleturquoise',
                align='left'),
    cells=dict(values=[combined_with_home_price_df[col] for col in combined_with_home_price_df.columns],
               fill_color='lavender',
               align='left'))
])

# Update layout
fig.update_layout(title='Interactive Table for all Job Postings')

# Show the table
fig.show()

In [16]:

# Filter the DataFrame based on the requirement
filtered_df = combined_with_home_price_df[combined_with_home_price_df['avg_annual_salary'] > combined_with_home_price_df['Avg_Median_Income']]

# Create the table
fig = go.Figure(data=[go.Table(
    header=dict(values=list(filtered_df.columns),
                fill_color='paleturquoise',
                align='left'),
    cells=dict(values=[filtered_df[col] for col in filtered_df.columns],
               fill_color='lavender',
               align='left'))
])

# Update layout
fig.update_layout(title='Interactive Table for Job Postings where Average Salary > Average Median Income')

# Show the table
fig.show()

## Create Dashboard

In [40]:
def calculate_monthly_payment(principal, annual_interest_rate, loan_term_years):
    # Convert annual interest rate to monthly rate
    monthly_interest_rate = annual_interest_rate / 12 / 100
    
    # Convert loan term from years to months
    loan_term_months = loan_term_years * 12
    
    # Calculate monthly mortgage payment using the formula
    monthly_payment = principal * (monthly_interest_rate * (1 + monthly_interest_rate) ** loan_term_months) / ((1 + monthly_interest_rate) ** loan_term_months - 1)
    
    return monthly_payment

In [45]:
# Initialize the Dash app
app = dash.Dash(__name__)

# Define the app layout
app.layout = html.Div(style={'backgroundColor': 'lightgray', 'padding': '20px'}, children=[
    html.H1('Job Listings and Mortgage Payment Dashboard', style={'textAlign': 'center'}),
    html.Div([
        html.Label('Select a County:'),
        dcc.Dropdown(
            id='county-dropdown',
            options=[{'label': county, 'value': county} for county in combined_with_home_price_df['County'].unique()],
            value=None
        ),
        html.Div(id='job-listings', style={'marginTop': '20px', 'textAlign': 'center'})
    ], style={'maxWidth': '1000px', 'margin': 'auto', 'marginTop': '20px'}),
    html.Div([
        html.Label('Select a Job:'),
        dcc.Dropdown(
            id='job-dropdown',
            value=None
        ),
        html.Div(id='average-salary-output', style={'marginTop': '20px'})
    ]),
    html.Div([
        html.Label('Estimated Mortgage Payment:'),
        html.Div(id='mortgage-output', style={'marginTop': '20px'})
    ])
])

# Define callback to update job listings based on selected county
@app.callback(
    Output('job-listings', 'children'),
    [Input('county-dropdown', 'value')]
)
def update_job_listings(selected_county):
    if selected_county is None:
        return html.Div()

    # Filter job listings based on selected county and salary criteria
    filtered_jobs = combined_with_home_price_df[
        (combined_with_home_price_df['County'] == selected_county) &
        (combined_with_home_price_df['avg_annual_salary'] > combined_with_home_price_df['Avg_Median_Income'])
    ]

    # Create a table to display job listings
    job_listings_table = html.Table(
        # Table header
        [html.Tr([html.Th(col) for col in filtered_jobs.columns])] +
        # Table body
        [html.Tr([html.Td(filtered_jobs.iloc[i][col]) for col in filtered_jobs.columns]) for i in range(len(filtered_jobs))],
        style={'margin': 'auto'}  # Center-align the table
    )

    return job_listings_table

# Define callback to update the job dropdown options based on selected county
@app.callback(
    Output('job-dropdown', 'options'),
    [Input('county-dropdown', 'value')]
)
def update_job_options(selected_county):
    if selected_county is None:
        return []

    # Filter job titles based on selected county
    job_options = [{'label': title, 'value': title} for title in combined_with_home_price_df.loc[combined_with_home_price_df['County'] == selected_county, 'working_title'].unique()]

    return job_options

# Define callback to update average monthly salary based on selected job
@app.callback(
    Output('average-salary-output', 'children'),
    [Input('county-dropdown', 'value'),
     Input('job-dropdown', 'value')]
)
def update_average_salary_output(selected_county, selected_job):
    if selected_county is None or selected_job is None:
        return ''

    # Calculate the average monthly salary for the selected job in the selected county
    average_salary = combined_with_home_price_df[(combined_with_home_price_df['County'] == selected_county) & (combined_with_home_price_df['working_title'] == selected_job)]['avg_annual_salary'].mean() / 12

    return f'${average_salary:.2f}'

# Define callback to update the estimated mortgage payment based on selected county
@app.callback(
    Output('mortgage-output', 'children'),
    [Input('county-dropdown', 'value')]
)
def update_mortgage_output(selected_county):
    if selected_county is None:
        return ''

    # Get the average home price for the selected county
    avg_home_price = combined_with_home_price_df.loc[combined_with_home_price_df['County'] == selected_county, 'Home_Price_Average'].mean()

    # Calculate the estimated monthly mortgage payment
    estimated_monthly_payment = calculate_monthly_payment(avg_home_price, annual_interest_rate=6, loan_term_years=30)

    return f'${estimated_monthly_payment:.2f}'

if __name__ == '__main__':
    app.run_server(debug=True)

In [ ]:
# Close the connection 
# cnx.close()
print("Connection closed")